In [11]:
import requests
from bs4 import BeautifulSoup
import json
import csv

def fetch_details_from_animal_page(animal_url):
    """
    Fetches "Facts" for a single animal from its page.
    """
    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3'}
    try:
        response = requests.get(animal_url, headers=headers)
        if response.status_code == 404:
            print(f"Error: Page not found for {animal_url}")
            return {"Error": "Page not found"}
        response.raise_for_status()
        soup = BeautifulSoup(response.content, "html.parser")
        
        # Initialize the dictionaries to hold facts
        details = {"Facts": {}}
        
        # Function to fetch details based on section title
        def fetch_section_details(section_title):
            section_data = {}
            section_heading = soup.find("h2", string=lambda text: section_title.lower() in text.lower())
            if section_heading:
                dl = section_heading.find_next("dl")
                if dl:
                    # Iterate through all dt and dd pairs within the dl
                    for dt, dd in zip(dl.find_all("dt"), dl.find_all("dd")):
                        key = dt.get_text(strip=True).strip(':')
                        value = dd.get_text(strip=True)
                        section_data[key] = value
            return section_data
        
        # Fetch "Facts"
        details["Facts"] = fetch_section_details("Facts")
            
        return details
    except requests.exceptions.RequestException as e:
        return {"Error": f"Request error: {str(e)}"}
    except Exception as e:
        return {"Error": str(e)}

def fetch_characteristics_from_animal_page(animal_url):
    """
    Fetches "Characteristics" for a single animal from its page.
    """
    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3'}
    try:
        response = requests.get(animal_url, headers=headers)
        if response.status_code == 404:
            print(f"Error: Page not found for {animal_url}")
            return {"Error": "Page not found"}
        response.raise_for_status()
        soup = BeautifulSoup(response.content, "html.parser")
        
        # Initialize the dictionary to hold characteristics
        details = {"Characteristics": {}}
        
        # Function to fetch details based on section title
        def fetch_section_details(section_title):
            section_data = {}
            section_heading = soup.find("h2", string=lambda text: section_title.lower() in text.lower())
            if section_heading:
                dl = section_heading.find_next("dl")
                if dl:
                    # Iterate through all dt and dd pairs within the dl
                    for dt, dd in zip(dl.find_all("dt"), dl.find_all("dd")):
                        key = dt.get_text(strip=True).strip(':')
                        value = dd.get_text(strip=True)
                        section_data[key] = value
            return section_data
        
        # Fetch "Characteristics"
        details["Characteristics"] = fetch_section_details("Characteristics")
        
        return details
    except requests.exceptions.RequestException as e:
        return {"Error": f"Request error: {str(e)}"}
    except Exception as e:
        return {"Error": str(e)}

def fetch_animals_by_state(state_name):
    """
    Fetches the list of animals and their details for a specific state.
    """
    formatted_state_name = state_name.lower().replace(" ", "-")
    url = f"https://a-z-animals.com/animals/location/north-america/united-states/{formatted_state_name}/"
    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3'}

    try:
        response = requests.get(url, headers=headers)
        if response.status_code == 404:
            print(f"Error fetching animal list for {state_name}: Page not found")
            return {}
        response.raise_for_status()
        soup = BeautifulSoup(response.content, "html.parser")
        title_element = soup.find("h2", string=lambda text: "animals list" in text.lower())
        if not title_element:
            return {}
        
        container_element = title_element.find_next("div")
        if not container_element:
            return {}
        
        animal_details = {}
        animal_elements = container_element.find_all("li")
        for li in animal_elements:
            animal_name = li.get_text(strip=True)
            # Construct the animal page URL here based on observed patterns or extract from the list element
            animal_url = f"https://a-z-animals.com/animals/{animal_name.lower().replace(' ', '-')}/"
            details = fetch_details_from_animal_page(animal_url)
            if isinstance(details, dict):
                details['Animal URL'] = animal_url
                animal_details[animal_name] = details
        
        return animal_details
    
    except requests.exceptions.RequestException as e:
        print(f"Error fetching animal list for {state_name}: {str(e)}")
        return {}
    except Exception as e:
        print(f"Unexpected error for state {state_name}: {str(e)}")
        return {}
    
    return details

def fetch_all_states_animal_lists():
    """
    Fetches the list of animals and their details for all states.
    """
    states = ['Alabama', 'Alaska', 'American Samoa', 'Arizona', 'Arkansas', 'California', 'Colorado', 'Connecticut', 'Delaware', 'District of Columbia', 'Florida', 'Georgia', 'Guam', 'Hawaii', 'Idaho', 'Illinois', 'Indiana', 'Iowa', 'Kansas', 'Kentucky', 'Louisiana', 'Maine', 'Maryland', 'Massachusetts', 'Michigan', 'Minnesota', 'Mississippi', 'Missouri', 'Montana', 'Nebraska', 'Nevada', 'New Hampshire', 'New Jersey', 'New Mexico', 'New York', 'North Carolina', 'North Dakota', 'Northern Mariana Islands', 'Ohio', 'Oklahoma', 'Oregon', 'Pennsylvania', 'Puerto Rico', 'Rhode Island', 'South Carolina', 'South Dakota', 'Tennessee', 'Texas', 'U.S. Virgin Islands', 'United States Minor Outlying Islands', 'Utah', 'Vermont', 'Virginia', 'Washington', 'West Virginia', 'Wisconsin', 'Wyoming']
    all_animals = {}

    for state in states:
        animals_list = fetch_animals_by_state(state)
        all_animals[state] = animals_list
        print(f"Fetched animals for {state}")
        
        if animals_list: 
            # Printing the details for each animal
            for animal, details in animals_list.items():
                print(f"Animal: {animal}")
                print("Facts:")
                print(json.dumps(details.get('Facts', {}), indent=4))
                print("Characteristics:")
                characteristics = fetch_characteristics_from_animal_page(details['Animal URL'])
                print(json.dumps(characteristics.get('Characteristics', {}), indent=4))
                print("\n")
        else:
            print(f"No animal data found for {state}") 
            
    return all_animals

# Fetch and print the list of animals for all states
all_states_animals = fetch_all_states_animal_lists()
print(json.dumps(all_states_animals, indent=4))

Error: Page not found for https://a-z-animals.com/animals/albino-(amelanistic)-corn-snake/
Error: Page not found for https://a-z-animals.com/animals/groundhog-(woodchuck)/
Error: Page not found for https://a-z-animals.com/animals/smallmouth-bass/
Fetched animals for Alabama
Animal: Admiral Butterfly
Facts:
{
    "Name Of Young": "Larvae",
    "Group Behavior": "Solitary/Group",
    "Fun Fact": "Admiral butterflies are named for their wing patterns, which resemble military insignia!",
    "Biggest Threat": "Habitat loss",
    "Most Distinctive Feature": "Flashy wing colors and patterns",
    "Wingspan": "1.75 to 3.9 inches",
    "Habitat": "Forests, fields, jungles, mountain ranges, orchards, near streams and marshes, urban areas",
    "Predators": "Monkeys, birds, rats, snakes, frogs, toads, lizards, dragonflies, wasps, ants, flies, spiders",
    "Diet": "Herbivore",
    "Lifestyle": "Diurnal",
    "Favorite Food": "Nectar, rotting fruit, carcasses, urine, excrement",
    "Special Feat

{
    "Color": "YellowBlue",
    "Skin Type": "Scales",
    "Venomous": "No",
    "Aggression": "Medium"
}


Animal: Brown Water Snake
Facts:
{
    "Prey": "Fish",
    "Fun Fact": "Has more scales than any other water snake on the continent: 27 to 33 rows of dorsal scales!",
    "Other Name(s)": "Water rattle, southern water snake, pied water snake, greater water snake, water-pilot, aspic, and false moccasin",
    "Litter Size": "Up to 61, but typically 20-30",
    "Diet": "Omnivore",
    "Type": "Reptile",
    "Common Name": "Brown water snake, brown watersnake"
}
Characteristics:
{
    "Color": "Brown",
    "Skin Type": "Scales",
    "Lifespan": "Up to 9 years in captivity",
    "Length": "3.5-6 ft"
}


Animal: Cane Spider
Facts:
{
    "Prey": "Insects, arachnids and small mammals",
    "Main Prey": "Butterfly, moths, and cockroaches",
    "Name Of Young": "Caterpillar",
    "Group Behavior": "Solitary",
    "Fun Fact": "Cane spiders don't spin webs to catch prey",
    "Most Distinct

{
    "Color": "BrownGreyBlackWhiteTan",
    "Skin Type": "Scales",
    "Lifespan": "15-20+ years",
    "Length": "2-8 feet",
    "Venomous": "Yes",
    "Aggression": "Medium"
}


Animal: Eastern Fence Lizard
Facts:
{
    "Prey": "insects, arachnids, and arthropods",
    "Name Of Young": "hatchling",
    "Group Behavior": "Solitary",
    "Fun Fact": "Females are usually larger than males.",
    "Estimated Population Size": "over 1,000,000",
    "Biggest Threat": "habitat loss",
    "Most Distinctive Feature": "spiny scales, wavelike markings",
    "Other Name(s)": "fence lizard, plateau lizard, prairie lizard",
    "Gestation Period": "8-10 weeks",
    "Litter Size": "3-16",
    "Habitat": "forest, grassland, and shrublands",
    "Predators": "snakes, birds, larger lizards, cats",
    "Diet": "Carnivore",
    "Lifestyle": "Diurnal",
    "Type": "reptile",
    "Common Name": "Eastern fence lizard",
    "Number Of Species": "7",
    "Location": "parts of the United States, Mexico",
    "

{
    "Color": "BrownGrey-Brown",
    "Skin Type": "Fur",
    "Top Speed": "17 mph",
    "Lifespan": "6-12.6 years",
    "Length": "21 inches",
    "Age of Sexual Maturity": "10-11 months",
    "Age of Weaning": "2 months"
}


Animal: Groundhog (Woodchuck)
Facts:
{}
Characteristics:
Error: Page not found for https://a-z-animals.com/animals/groundhog-(woodchuck)/
{}


Animal: Indigo Snake
Facts:
{
    "Prey": "Snakes, mammals, reptiles",
    "Group Behavior": "Solitary",
    "Fun Fact": "Indigo snakes use brute force to overpower their prey.",
    "Diet": "Carnivore",
    "Average Litter Size": "4 to 12 eggs",
    "Lifestyle": "Diurnal",
    "Common Name": "Indigo snake",
    "Location": "North America, Central America, South America"
}
Characteristics:
{
    "Lifespan": "Unknown",
    "Height": "Snakes, mammals, reptiles",
    "Length": "7 to 9 feet"
}


Animal: Jack Crevalle
Facts:
{
    "Main Prey": "Smaller fishes",
    "Name Of Young": "Fry",
    "Group Behavior": "Solitary/School"

{
    "Color": "GreyYellowBlackDull Olive",
    "Skin Type": "Feathers",
    "Lifespan": "Oldest recorded individual was 7.9 years old.",
    "Weight": "Average 0.45 ounces",
    "Length": "Average about 5.2 inches",
    "Age of Sexual Maturity": "1 year",
    "Venomous": "No",
    "Aggression": "Medium"
}


Animal: Needlefish
Facts:
{
    "Prey": "crustaceans, small fish, frogs, insects",
    "Group Behavior": "School",
    "Fun Fact": "no stomach to digest food",
    "Estimated Population Size": "unknown",
    "Biggest Threat": "fishing",
    "Most Distinctive Feature": "long serrated beak",
    "Other Name(s)": "long toms",
    "Gestation Period": "10-15 days",
    "Optimum pH Level": "6-8",
    "Habitat": "bays, inlets, rivers",
    "Predators": "tuna, dolphins, humans",
    "Diet": "Carnivore",
    "Type": "belonidae",
    "Common Name": "needlefish, garfish",
    "Number Of Species": "60"
}
Characteristics:
{
    "Color": "BlueWhiteGreenSilver",
    "Skin Type": "Scales",
    "To

...

{
    "Color": "BrownBlack",
    "Skin Type": "Exoskeleton",
    "Top Speed": "3 mph",
    "Lifespan": "2-6 months",
    "Weight": "0.105 g",
    "Height": "0.25 in",
    "Length": "1.5 in",
    "Age of Sexual Maturity": "90-100 days"
}


Animal: Smooth Earth Snake
Facts:
{
    "Prey": "Earthworms and soft-bodied arthropods including larvae",
    "Name Of Young": "Neonate, snakelet",
    "Group Behavior": "Solitary except during mating season",
    "Fun Fact": "Valeria Biddle Blaney (1828-1900) collected the first specimen in Maryland.",
    "Most Distinctive Feature": "Small black ring around the eye and white chin",
    "Litter Size": "3-12",
    "Diet for this Fish": "Omnivore",
    "Lifestyle": "Nocturnal/Crepuscular",
    "Location": "Eastern and southeastern United States"
}
Characteristics:
{
    "Color": "BrownFawn",
    "Skin Type": "Scales",
    "Length": "7-9.8 inches",
    "Venomous": "No",
    "Aggression": "Low"
}


Animal: Swallowtail Butterfly
Facts:
{
    "Prey": "plan

{
    "Color": "BrownBlackPurple"
}


Animal: Blue Racer
Facts:
{
    "Prey": "Insects, rodents, small birds, frogs, snakes",
    "Name Of Young": "Snakelets or hatchlings",
    "Fun Fact": "Some blue racers have smooth scales that are solid electric blue while others are grayish or brownish.",
    "Estimated Population Size": "1,000,000",
    "Biggest Threat": "These snakes are endangered in Canada because they are losing their field and meadow habitat to construction and farmland expansion.",
    "Most Distinctive Feature": "Its beautiful, electric blue scales",
    "Distinctive Feature": "Its ability to move at over 4 miles per hour!",
    "Habitat": "Open meadows, prairies, and pond shorelines",
    "Diet": "Omnivore",
    "Type": "Snake",
    "Common Name": "Blue racer"
}
Characteristics:
{
    "Skin Type": "Scales",
    "Venomous": "No",
    "Aggression": "Low"
}


Animal: Cinnamon Bear
Facts:
{
    "Prey": "Berries, nuts, vegetation, small rodents, insects, fish",
    "Main Prey

{
    "Color": "BrownGreyBlackTan",
    "Skin Type": "Scales",
    "Lifespan": "8-14 years",
    "Length": "24-30 inches"
}


Animal: Mealybug
Facts:
{
    "Name Of Young": "Nymphs or instars",
    "Group Behavior": "Colony",
    "Fun Fact": "They have a symbiotic relationship with ants.",
    "Biggest Threat": "Poisonous plants",
    "Most Distinctive Feature": "Waxy, mealy appearance",
    "Gestation Period": "4-6 days",
    "Litter Size": "100-600 eggs depending on species",
    "Habitat": "Plants",
    "Diet": "Herbivore",
    "Type": "Insect",
    "Common Name": "Mealybugs",
    "Location": "Worldwide"
}
Characteristics:
{
    "Color": "YellowWhite",
    "Skin Type": "Exoskeleton",
    "Lifespan": "68 days or 7-10 weeks",
    "Length": "2mm (male); 4mm (female)",
    "Age of Sexual Maturity": "20-44 days depending on species"
}


Animal: Miki
Facts:
{
    "Fun Fact": "They can be trained to use the litter box like a cat!",
    "Temperament": "Sweet and intelligent",
    "Diet": "O

{
    "Color": "BrownGreyYellowWhite",
    "Skin Type": "Scales",
    "Lifespan": "5-10 years in the wild, up to 20 in captivity",
    "Length": "Up to 24\u201d",
    "Venomous": "No",
    "Aggression": "Low"
}


Animal: Rat Snakes
Facts:
{
    "Prey": "Rats, mice, birds, bird eggs, lizards",
    "Main Prey": "Rats and mice",
    "Name Of Young": "Hatchlings",
    "Group Behavior": "Solitary",
    "Fun Fact": "Rat snakes are constrictors from the Colubridae family of snakes.",
    "Biggest Threat": "Vehicles on roads, human encroachment",
    "Other Name(s)": "Corn snake, rat snake, bush snake,",
    "Gestation Period": "2-3 months",
    "Temperament": "Generally mellow, but some species are more aggressive.",
    "Litter Size": "Anywhere from 3-20 eggs",
    "Habitat": "Dense rainforest jungles to arid deserts.",
    "Diet for this Fish": "Carnivore",
    "Lifestyle": "Diurnalor Nocturnal Depending on Region and Season",
    "Number Of Species": "50",
    "Average Clutch Size": "12",


{
    "Color": "BrownGreyYellowFawnBlueBlackWhiteTanDark BrownCreamOrangeChocolate",
    "Skin Type": "Exoskeleton",
    "Lifespan": "2-4 weeks",
    "Weight": "0.0014 - 0.0105 ounces",
    "Height": "1-2 inches",
    "Length": "2-4 inch wingspan",
    "Age of Sexual Maturity": "approx. 1-2 weeks",
    "Age of Weaning": "N/A",
    "Venomous": "No",
    "Aggression": "Medium"
}


Animal: Tree Cricket
Facts:
{
    "Prey": "Soft-bodied insects like aphids",
    "Name Of Young": "Nymph",
    "Group Behavior": "Mainly solitary",
    "Fun Fact": "The music of tree crickets is typically lower in pitch than the music produced by other cricket subfamilies!",
    "Biggest Threat": "Habitat loss",
    "Most Distinctive Feature": "Ability to make musical noises with their wings",
    "Other Name(s)": "Pale bush cricket",
    "Habitat": "Trees, shrubs, herbs",
    "Predators": "Birds, small mammals, reptiles, amphibians, other insects, spiders",
    "Diet": "Omnivore",
    "Lifestyle": "Nocturnal",

In [48]:
import requests
from bs4 import BeautifulSoup
import os

def fetch_images(base_url, output_folder):
    """
    Fetches images under the title "American Animals" from the given URL.
    Saves the images with the animal name in the output folder.
    """
    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3'}

    response = requests.get(base_url, headers=headers)
    soup = BeautifulSoup(response.content, "html.parser")
    
    # Find the container of the "American Animals"
    container = soup.find("h2", string="American Animals").find_next_sibling("div", class_="row")
    
    if not container:
        print("Could not find the American Animals container.")
        return
    
    # Find all the cards containing animals
    cards = container.find_all("div", class_="card")
    
    for card in cards:
        # The animal name is within the <h5> tag
        animal_name_tag = card.find("h5", class_="card-title")
        if animal_name_tag:
            animal_name = animal_name_tag.get_text(strip=True)
            
            # The image is within the <a> tag that contains the URL to the animal's page
            image_tag = card.find("img")
            if image_tag and image_tag.has_attr('src'):
                image_url = image_tag['src']               
                image_response = requests.get(image_url, headers=headers)
                safe_animal_name = animal_name.replace(" ", "_").replace("/", "_or_")
                image_name = os.path.join(output_folder, safe_animal_name + ".jpg")
                
                try:
                    with open(image_name, 'wb') as file:
                        file.write(image_response.content)
                    print(f"Saved image for {animal_name}")
                except FileNotFoundError as e:
                    print(f"Could not save image for {animal_name}: {e}")

base_url = "https://a-z-animals.com/animals/location/north-america/united-states/"
output_folder = "C:/Users/Antonela/finalProjDV/datasets/img"

if not os.path.exists(output_folder):
    os.makedirs(output_folder)

fetch_images(base_url, output_folder)


Saved image for Acadian Flycatcher
Saved image for Admiral Butterfly
Saved image for Agkistrodon Contortrix
Saved image for Agouti
Saved image for Akita Shepherd
Saved image for Alaskan Husky
Saved image for Alaskan Klee Kai
Saved image for Alaskan Malamute
Saved image for Alaskan Pollock
Saved image for Alaskan Shepherd
Saved image for Albatross
Saved image for Albino (Amelanistic) Corn Snake
Saved image for American Alligator
Saved image for Alligator Gar
Saved image for Allosaurus
Saved image for Allosaurus
Saved image for Alpine Goat
Saved image for Alusky
Saved image for Ambrosia Beetle
Saved image for American Alsatian
Saved image for American Bulldog
Saved image for American Bully
Saved image for American Cocker Spaniel
Saved image for American Cockroach
Saved image for American Coonhound
Saved image for American Dog Tick
Saved image for American Eel
Saved image for American Eskimo Dog
Saved image for American Foxhound
Saved image for American Hairless Terrier
Saved image for Am

Saved image for Cougar
Saved image for Cow
Saved image for Coyote
Saved image for Crab
Saved image for Crab Spider
Saved image for Crane
Saved image for Cricket
Saved image for Crocodile
Saved image for Crocodylomorph
Saved image for Cross Fox
Saved image for Crow
Saved image for Cuckoo
Saved image for Cucumber Beetle
Saved image for Dachsador
Saved image for Dachshund Mix
Saved image for Daeodon
Saved image for Dalmador
Saved image for Daniff
Saved image for Dark-Eyed Junco
Saved image for Dark-Eyed Junco
Saved image for Daug
Saved image for De Kay’s Brown Snake
Saved image for Death’s Head Cockroach
Saved image for Deathwatch Beetle
Saved image for Deer
Saved image for Deer Mouse
Saved image for Deer Tick
Saved image for Deinosuchus
Saved image for Desert Kingsnake
Saved image for Desmostylus
Saved image for Diamondback Moth
Saved image for Dickcissel
Saved image for Dilophosaurus
Saved image for Dimetrodon
Saved image for Diplodocus
Saved image for Dire Wolf
Saved image for Diving D

Saved image for Leafcutter Ant
Saved image for Least Flycatcher
Saved image for Leatherback Sea Turtle
Saved image for Leech
Saved image for Leghorn Chicken
Saved image for Leopard Frog
Saved image for Leopard Lizard
Saved image for Lesser Scaup
Saved image for Lhasapoo
Saved image for Liger
Saved image for Lineback Cattle
Saved image for Little Brown Bat
Saved image for Lizard
Saved image for Lizardfish
Saved image for Loach
Saved image for Loggerhead Shrike
Saved image for Lone Star Tick
Saved image for Long-Eared Owl
Saved image for Longnose Gar
Saved image for Lynx
Saved image for MacGillivray’s Warbler
Saved image for Machaeroides
Saved image for Mackenzie Valley Wolf
Saved image for Maggot
Saved image for Magnolia Warbler
Saved image for Mahi Mahi (Dolphin Fish)
Saved image for Maiasaura
Saved image for Maine Coon
Saved image for Mal Shi
Saved image for Malchi
Saved image for Mallard
Saved image for Maltipom
Saved image for Marans Chicken
Saved image for Marble Fox
Saved image fo

Saved image for Savanna Goat
Saved image for Savannah Sparrow
Saved image for Scarlet Kingsnake
Saved image for Schneagle
Saved image for Scissor-tailed Flycatcher
Saved image for Scorpion
Saved image for Scottish Fold Cat
Saved image for Sculpin
Saved image for Sea Bass
Saved image for Sea Eagle
Saved image for Sea Roach
Saved image for Seagull
Saved image for Seahorse
Saved image for Senepol Cattle
Saved image for Sharp-Shinned Hawk
Saved image for Sharp-Tailed Snake
Saved image for Sheep
Saved image for Sheepshead Fish
Saved image for Shepadoodle
Saved image for Shepweiler
Saved image for Shichi
Saved image for Shih Poo
Saved image for Shiloh Shepherd
Saved image for Shiranian
Saved image for Shollie
Saved image for Short-Eared Owl
Saved image for Short-Faced Bear
Saved image for Shrew
Saved image for Shrimp
Saved image for Siberian Husky
Saved image for Sidewinder
Saved image for Silken Windhound
Saved image for Silver Labrador
Saved image for Skink Lizard
Saved image for Skunk
Sav

In [12]:
import csv

# Define the CSV file path
csv_file_path = "C:/Users/Antonela/finalProjDV/datasets/us-animals-listed.csv"

# Write data to CSV
with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
    writer = csv.writer(file)
    
    # Write the header
    writer.writerow(['State', 'Animal Name', 'Facts', 'Characteristics'])
    
    # Write the data
    for state, animals in all_states_animals.items():            
        if isinstance(animals, dict):
            for animal_name, details in animals.items():
                facts = json.dumps(details.get('Facts', ''))
                characteristics = json.dumps(fetch_characteristics_from_animal_page(details['Animal URL']).get('Characteristics', {}))
                writer.writerow([state, animal_name, facts, characteristics])


print(f"Data has been written to {csv_file_path}")


Error: Page not found for https://a-z-animals.com/animals/albino-(amelanistic)-corn-snake/
Error: Page not found for https://a-z-animals.com/animals/groundhog-(woodchuck)/
Error: Page not found for https://a-z-animals.com/animals/smallmouth-bass/
Error: Page not found for https://a-z-animals.com/animals/bumblebee/
Error: Page not found for https://a-z-animals.com/animals/glowworm/
Error: Page not found for https://a-z-animals.com/animals/groundhog-(woodchuck)/
Error: Page not found for https://a-z-animals.com/animals/rainbow-grasshopper-(dactylotum-bicolor)/


Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.


Error: Page not found for https://a-z-animals.com/animals/mexican-eagle-(northern-crested-caracara)/
Error: Page not found for https://a-z-animals.com/animals/rainbow-grasshopper-(dactylotum-bicolor)/
Error: Page not found for https://a-z-animals.com/animals/redear-sunfish/
Error: Page not found for https://a-z-animals.com/animals/smallmouth-bass/
Error: Page not found for https://a-z-animals.com/animals/albino-(amelanistic)-corn-snake/
Error: Page not found for https://a-z-animals.com/animals/groundhog-(woodchuck)/
Error: Page not found for https://a-z-animals.com/animals/pygmy-rattlesnake/
Error: Page not found for https://a-z-animals.com/animals/rainbow-grasshopper-(dactylotum-bicolor)/
Error: Page not found for https://a-z-animals.com/animals/smallmouth-bass/
Error: Page not found for https://a-z-animals.com/animals/chilean-recluse-spider/
Error: Page not found for https://a-z-animals.com/animals/opaleye-(rudderfish)/
Error: Page not found for https://a-z-animals.com/animals/rainbo

Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.


Error: Page not found for https://a-z-animals.com/animals/ornate-black-tailed-rattlesnake/
Error: Page not found for https://a-z-animals.com/animals/rainbow-grasshopper-(dactylotum-bicolor)/
Error: Page not found for https://a-z-animals.com/animals/smallmouth-bass/
Error: Page not found for https://a-z-animals.com/animals/groundhog-(woodchuck)/
Error: Page not found for https://a-z-animals.com/animals/redear-sunfish/
Error: Page not found for https://a-z-animals.com/animals/smallmouth-bass/
Error: Page not found for https://a-z-animals.com/animals/albino-(amelanistic)-corn-snake/
Error: Page not found for https://a-z-animals.com/animals/groundhog-(woodchuck)/
Error: Page not found for https://a-z-animals.com/animals/harlequin-coral-snake/
Error: Page not found for https://a-z-animals.com/animals/pygmy-rattlesnake/
Error: Page not found for https://a-z-animals.com/animals/redear-sunfish/
Error: Page not found for https://a-z-animals.com/animals/smallmouth-bass/
Error: Page not found for

Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.


Error: Page not found for https://a-z-animals.com/animals/harlequin-coral-snake/
Error: Page not found for https://a-z-animals.com/animals/mexican-eagle-(northern-crested-caracara)/
Error: Page not found for https://a-z-animals.com/animals/ornate-black-tailed-rattlesnake/
Error: Page not found for https://a-z-animals.com/animals/pygmy-rattlesnake/
Error: Page not found for https://a-z-animals.com/animals/rainbow-grasshopper-(dactylotum-bicolor)/
Error: Page not found for https://a-z-animals.com/animals/smallmouth-bass/
Error: Page not found for https://a-z-animals.com/animals/rainbow-grasshopper-(dactylotum-bicolor)/
Error: Page not found for https://a-z-animals.com/animals/smallmouth-bass/
Error: Page not found for https://a-z-animals.com/animals/groundhog-(woodchuck)/
Error: Page not found for https://a-z-animals.com/animals/redear-sunfish/
Error: Page not found for https://a-z-animals.com/animals/albino-(amelanistic)-corn-snake/
Error: Page not found for https://a-z-animals.com/anim